In [ ]:
#finn ut hvor stor prosentandel av turene hver hexagon har for hver dag
# Calculate the total number of trips for each hexagon
total_trips = sum(hexagon.depatures for hexagon in hexagons)

# Calculate the percentage of trips for each hexagon for each day
for i in range(7): 
    
    for hexagon in hexagons:
        hexagon_percentage = (hexagon.depatures / total_trips) * 100
        print(f"Hexagon {hexagon.hex_id}: {hexagon_percentage:.2f}%")

percentage_trips = []
for hexagon in hexagons:
    hexagon_percentage = [round((count / hexagon.depatures) * 100, 2) if hexagon.depatures != 0 else 0 for count in hexagon.initial_target_state]
    percentage_trips.append(hexagon_percentage)

# Print the percentage of trips for each hexagon for each day
for i, hexagon in enumerate(hexagons):
    print(f"Hexagon {hexagon.hex_id}: {percentage_trips[i]}")


In [59]:

WEEKS = 3

import random
import h3
from random import randint, sample
import requests
from shapely.geometry import Point, Polygon
from datetime import datetime, timezone
import numpy as np
import geopy.distance
import folium
import json
from json_settings import *
import gzip
import math

class HexWeb:
    def __init__(self, lat, lng):
        self.lat = lat
        self.lng = lng
        self.center = lat, lng
        self.hexagons = None
        self.total_average_intitial_state = [0 for i in range(7)]
        self.round_total_average_intitial_state = [0 for i in range(7)]
        self.day_week = {}
        self.total_scooters = 1066

    
    def distribute_rest_scooters(self):
        for day in range(7):
            for hexagon in self.hexagons:
                hexagon.final_target_state[day] = int(hexagon.round_average_initial_target_state[day] / self.round_total_average_intitial_state[day] * self.total_scooters)
                

    def count_depatures(self):
        print("teller total depatures")
        for hexagon in self.hexagons:
            hexagon.do_average_initial_target_state()
            for i in range(7): 
                self.total_average_intitial_state[i][j] += hexagon.average_initial_target_state[i]
                self.round_total_average_intitial_state[i] += hexagon.round_average_initial_target_state[i]

    
    def generate_hex_web_from_json(self, data):
        hexagons = []
        # hex_id = 0
        for hex_data in data['areas']:
            hex_id = hex_data['id']
            # hex_id += 1
            vertices = hex_data['edges']  # Bruker 'edges' som vertices
            center = hex_data['location']  # Bruker 'location' som center
            hexagon = Hexagon(hex_id, vertices, center)
            hexagons.append(hexagon)
        self.hexagons = hexagons
        return hexagons

   # def map(self): 
        # Create a map centered around the given coordinates

      #  mymap = folium.Map(location=[self.lat, self.lng], zoom_start=13)  # Adjusted zoom level


       # lat, lng = 63.446827, 10.421906
       # resolution = 11 # Adjusted resolution level

        # Generate H3 index for the given coordinates at the specified resolution
       # index = h3.geo_to_h3(lat, lng, resolution)

        # Determine the hexagons within 1 ring from the center
       # hexagons = h3.k_ring(index, 100)

        # Plot the hexagons on the map
       # for hex in hexagons:
            # Get the vertices of the hexagon
       #    vertices = h3.h3_to_geo_boundary(hex, geo_json=True)
            # Folium requires reversing coordinates due to GeoJSON standard (lng, lat)
        #    vertices = [(v[1], v[0]) for v in vertices]
            # Create a hexagon object
            # Create a polygon and add to the map
        #    folium.Polygon(locations=vertices, fill=True, color="#ff7800", weight=2).add_to(mymap)

       # return mymap
    # Display the map

    def plot_and_save_depature_hexs(self, mymap):
        # Create a map centered around the given coordinates
        # Read JSON data from file
        with open('/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/3_weeks_sept.json', 'r') as file:
            data = json.load(file)

        # Plot trip coordinates as markers on the map
        for trip in data['data']:
            #print("ny tur")
            feature = trip['route']['features'][0]
            lng, lat = feature['geometry']['coordinates']
            start_time = trip["start_time"]
            start_time = datetime.fromtimestamp(start_time / 1000, tz=timezone.utc)

            device_id = trip["device_id"]
            #folium.Marker(location=[lat, lng], popup=trip['trip_id'], icon=folium.Icon(color='red')).add_to(mymap)
            
            

            start_hex = None
            start_coords = trip["route"]["features"][0]["geometry"]["coordinates"]
            start_coords = (start_coords[1], start_coords[0])
            if self.not_duplicate_scooter(start_time, device_id):
            

                for hex in self.hexagons:
                    if hex.is_point_inside(start_coords):
                        start_hex = hex
                        break
                    
                if start_hex is not None:
                    #print("funnet hex")
                    folium.CircleMarker(location=[lat, lng], radius=2, color='green', fill=True, fill_color='green').add_to(mymap)
                    start_hex.add_initial_target_state(start_time, device_id)
                    start_hex.count_depatures()

                #end_coords = trip["route"]["features"][-1]["geometry"]["coordinates"]
                #start_time = trip["start_time"]
                #end_time = trip["end_time"]

            #feature = trip['route']['features'][1]
            #lng, lat = feature['geometry']['coordinates']
            #folium.Marker(location=[lat, lng], popup=trip['trip_id'], icon=folium.Icon(color='blue')).add_to(mymap)
            #folium.CircleMarker(location=[lat, lng], radius=2, color='red', fill=True, fill_color='red').add_to(mymap)
        print("teller total depatures")
        self.count_depatures()
    
    def not_duplicate_scooter(self, start_dt, device_id):
        week_number = int(start_dt.strftime('%U'))
        weekday = start_dt.weekday()
        
        # Sjekk først om ukenummeret eksisterer i self.day_week, og initialiser hvis ikke
        if week_number not in self.day_week:
            self.day_week[week_number] = {}
            print(week_number)
        
        # Deretter, sjekk om det er en oppføring for den spesifikke dagen, initialiser til en tom liste hvis ikke
        if weekday not in self.day_week[week_number]:
            self.day_week[week_number][weekday] = []
            print(weekday)
        
        # Sjekk om device_id allerede finnes for gitt dag
        if device_id in self.day_week[week_number][weekday]:
           #print("duplikat")
            return False  # Dette er en duplikat
        else:
            # Legg til device_id siden dette er første gang scooter registreres denne dagen
            self.day_week[week_number][weekday].append(device_id)
            #print("ikke duplikat")
            
            return True  # Ikke en duplikat
  
    def write_to_file(self):
        json_data = {
        'areas': [
        {
            'id': hexagon.hex_id,  # A0
            # 'location': hexagon.center,  # [lat, lon]
            # 'initial_target_states': hexagon.average_initial_target_state,
            # 'round_initial_target_states': hexagon.round_average_initial_target_state,  # [[{id: value, ...} * 24] * 7]
            'final_target_states': hexagon.final_target_state,
        }
        for hexagon in self.hexagons
    ],
        'total_average_initial_state': self.total_average_intitial_state,
        'round_total_average_initial_state': self.round_total_average_intitial_state
}
        print("skriver til fil")
        file = '/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/initial_target_state_floor.json'
        
        with open(file, 'w') as file:
            json.dump(json_data, file, indent=4)
        print("skrevet til fil")
    

class Hexagon:
    "Lager et område, brukes til å telle arrivals/departures og move probabilities"
    def __init__(self, hex_id, vertices, center):
        self.hex_id = hex_id
        self.vertices = vertices
        self.center = center
        self.depatures = 0
        self.initial_target_state =  [0 for i in range(7)]
        self.average_initial_target_state = [0 for i in range(7)]
        self.round_average_initial_target_state = [0 for i in range(7)]
        self.final_target_state = [0 for i in range(7)]
        self.day_week = {}

    
    def count_depatures(self):
        self.depatures += 1
    
    def do_average_initial_target_state(self):
        for i in range(7):
            self.average_initial_target_state[i] = self.initial_target_state[i] / 3
            self.round_average_initial_target_state[i] = round(self.initial_target_state[i] / 3)
        return self.average_initial_target_state

    def add_initial_target_state(self, start_dt, device_id):
        #if timestamp is a monday add to index 0, if tuesday add to index 1, etc.
        
        day = start_dt.weekday()
        #print(day)
        self.initial_target_state[day] += 1


        
        
    def is_point_inside_boundingbox(self, bbox):
        lat, lon = self.center
        min_lon, max_lon, min_lat, max_lat = bbox
        return min_lon <= lon <= max_lon and min_lat <= lat <= max_lat

    def is_point_inside(self, location):
        polygon = Polygon(self.vertices)
        return polygon.contains(Point(location))
    



    

hex_data = None
FINISHED_DATA_FILE = "/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/TD_W19_test_W3.json.gz"
with gzip.open(FINISHED_DATA_FILE, 'rt', encoding='utf-8') as f:
    hex_data = json.load(f)


hexweb = HexWeb(63.431711, 10.403537)
print("created hexweb")
hexagons = hexweb.generate_hex_web_from_json(hex_data)
print("make hex")
mymap = folium.Map(location=[63.431711, 10.403537], zoom_start=13)  # Adjusted zoom level
hexweb.plot_and_save_depature_hexs(mymap)
hexweb.distribute_rest_scooters()
hexweb.write_to_file()
mymap


created hexweb
make hex
36
0
1
2
3
4
5
37
6
0
1
2
3
4
5
38
6
0
1
2
3
4
5
39
6
teller total depatures
teller total depatures
skriver til fil
skrevet til fil


In [60]:
with open('/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/initial_target_state_floor.json', 'r') as file:
    data = json.load(file)

final_target_states = [0 for i in range(7)]
        # Plot trip coordinates as markers on the map
for hex_data in data['areas']:
    hex_final_target_states = hex_data['final_target_states']

    for i in range(7):
        final_target_states[i] += hex_final_target_states[i]
    
print(final_target_states)
            

[767, 862, 866, 845, 796, 920, 1035]


In [11]:
FINISHED_DATA_FILE = "/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/TD_W19_test_W3.json.gz"
with gzip.open(FINISHED_DATA_FILE, 'rt', encoding='utf-8') as f:
    hex_data = json.load(f)

print
center1 = None
for hex_data in hex_data['areas']:
    #print(hex_data)  
    hex_id = hex_data['id']
    center = hex_data['location']
    if hex_id == "A5":
        center1 = center
    #elif hex_id == "A25743":
    #    print(center)

mymap = folium.Map(location=[63.431711, 10.403537], zoom_start=13)  # Adjusted zoom level
folium.CircleMarker(location=[center1[0],center1[1]], radius=2, color='green', fill=True, fill_color='green').add_to(mymap)
#folium.CircleMarker(location=[63.43200761264325, 10.407601420168318], radius=2, color='green', fill=True, fill_color='green').add_to(mymap)

mymap

TypeError: 'NoneType' object is not subscriptable

In [103]:
mymap = folium.Map(location=[63.431711, 10.403537], zoom_start=13)  # Adjusted zoom level
folium.CircleMarker(location=[63.43279534170655, 10.418034375205146], radius=2, color='green', fill=True, fill_color='green').add_to(mymap)
folium.CircleMarker(location=[63.43200761264325, 10.407601420168318], radius=2, color='green', fill=True, fill_color='green').add_to(mymap)

mymap


In [3]:
import json
import gzip
import folium

with open('/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/initial_target_state_1066.json', 'r') as file:
    data = json.load(file)

final_target_states = [0 for i in range(7)]
hot_spot_centers = []
     
for hex_data in data['areas']:  
    hex_final_target_states = hex_data['final_target_states']
    hex_id = hex_data['id']
    for i in range(7):
        final_target_states[i] += hex_final_target_states[i]
        if hex_final_target_states[i] > 3:
            hot_spot_centers.append(hex_id)

FINISHED_DATA_FILE = "/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/TD_W19_test_W3.json.gz"
with gzip.open(FINISHED_DATA_FILE, 'rt', encoding='utf-8') as f:
    hex_data = json.load(f)

mymap = folium.Map(location=[63.431711, 10.403537], zoom_start=13)  # Adjusted zoom level
for hex_data in hex_data['areas']:
    #print(hex_data)  
    hex_id = hex_data['id']
    center = hex_data['location']
    if hex_id in hot_spot_centers:
        folium.CircleMarker(location=[center[0],center[1]], radius=2, color='green', fill=True, fill_color='green').add_to(mymap)

mymap



In [93]:
with open('/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/finished_target_state_1066_json.json', 'r') as file:
    data = json.load(file)


final_target_states = [[0 for j in range(24)] for i in range(7)]
hex_data_dict = {}
targert_states = [[0 for i in range(24)] for j in range(7)]
     
for hex_data in data['areas']:  
    hex_final_target_states = hex_data['target_states']
    for i in range(7):
        for j in range(24):
            final_target_states[i][j] += hex_final_target_states[i][j]

#print(final_target_states)
for hex_data in data['areas']:
    hex_id = hex_data['id']
    hex_data_dict[hex_id] = hex_data['final_target_states']
    
        # Plot trip coordinates as markers on the map
print(final_target_states)

for i in range(7):
    for j in range(24):
        while final_target_states[i][j] != 1066:
            if final_target_states[i][j] > 1066:
                for hex_target_state in hex_data_dict.keys():
                    if hex_data_dict[hex_target_state][i][j] > 0:
                        hex_data_dict[hex_target_state][i][j] -= 1
                        final_target_states[i][j] -= 1
                        break
            elif final_target_states[i][j] < 1066:
                for hex_target_state in hex_data_dict.keys():
                    if final_target_states[i][j] < 1066:
                        if hex_data_dict[hex_target_state][i][j] > 0:
                            hex_data_dict[hex_target_state][i][j] += 1
                            final_target_states[i][j] += 1
                            break

print(final_target_states)

json_data = {
        'areas': [
        {
            'id': hex_target_state,  # A0
            # 'location': hexagon.center,  # [lat, lon]
            # 'initial_target_states': hexagon.average_initial_target_state,
            # 'round_initial_target_states': hexagon.round_average_initial_target_state,  # [[{id: value, ...} * 24] * 7]
            'final_target_states': hex_data_dict[hex_target_state],
        }
        for hex_target_state in hex_data_dict.keys()
    ],
      
        'total_average_initial_state': final_target_states
}
print("skriver til fil")
file = '/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/initial_target_state_1066.json'
        
with open(file, 'w') as file:
    json.dump(json_data, file, indent=4)
print("skrevet til fil")


9
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
6
3
3
3
6
6
3
3
6
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
6
3
3
3
3
9
3
3
3
3
3
6
5
3
3
12
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
9
6
3
3
3
5
3
3
3
3
3
3
9
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
6
3
3
3
3
3
6
3
3
3
3
3
3
9
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
6
3
3
3
3
3
3
3
3
6
3
9
3
5
3
3
3
3
3
3
3
3
6
9
3
3
3
3
3
3
3
3
3
3
3
3
3
3
9
3
3
3
3
3
3
5
3
6
3
3
3
6
6
3
3
3
6
6
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
9
6
9
3
9
3
3
3
3
9
3
3
3
3
3
3
3
6
3
3
3
3
3
3
3
6
3
9
3
3
3
12
3
8
5
5
3
6
3
9
3
3
3
3
3
6
3
3
3
3
9
3
3
3
3
3
3
3
3
3
5
3
12
3
3
3
3
3
3
3
3
3
6
3
3
3
3
3
3
3
3
9
3
3
3
3
3
6
3
3
3
3
3
6
3
3
3
3
3
3
3
3
3
3
3
3
3
6
3
3
9
3
3
6
3
6
3
3
3
3
3
3
9
3
3
3
3
3
9
3
3
19
3
3
6
3
3
3
3
3
3
3
3
3
3
3
3
3
3
9
3
3
6
3
3
3
3
3
3
3
3
3
3
6
9
3
3
3
3
3
9
3
3
3
3
3
3
9
3
3
3
3
3
3
3
3
6
9
3
3
3
3
3
3
3
3
3
3
3
6
3
3
3
3
3
3
3
3
6
3
5
3
9
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
5
3
3
6
3
3
3
3
3
3
3
3
3
5
3
3
3
3
3
5
3
6
3
3
3
3
3
3
5
3
3
3
3
3
3
3
3
3
3
5
3
6
3
3
6
3
3
6
3
3
9
3
3
3


In [ ]:
with gzip.open(FINISHED_DATA_FILE, 'rt', encoding='utf-8') as f:
    hex_data = json.load(f)

In [10]:
with open('/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/finished_target_state_1066_json.json', 'r') as file:
    data = json.load(file)

final_target_states = [[0 for j in range(24)] for i in range(7)]

for hex_data in data['areas']:
    #summer alle timer for hver dag og lagre i final_target_states
    hex_final_target_states = hex_data['target_states']
    #hex_id = hex_data['id']
    for i in range(7):
        for j in range(24):
            final_target_states[i][j] += hex_final_target_states[i][j]

print(final_target_states)

with open('/Users/elinehareide/Library/Mobile Documents/com~apple~CloudDocs/Desktop/Eline - Høst 2023/Prosjektoppgave/fomo/instances/Ryde/total_final_target_state_1066.json', 'w') as file:
    json.dump(final_target_states, file, indent=4)

[[1066, 1066, 1066, 1066, 1066, 1066, 3318, 3693, 3967, 4324, 4694, 4807, 4542, 4005, 3364, 2849, 2275, 1712, 1043, 417, 34, 3, 0, 0], [1066, 1066, 1066, 1066, 1066, 1066, 2846, 3249, 3678, 4091, 4565, 4668, 4400, 3760, 3124, 2687, 2351, 1775, 1007, 409, 23, 5, 1, 1], [1066, 1066, 1066, 1066, 1066, 1066, 2380, 2397, 2677, 3092, 3487, 3556, 3443, 3107, 2792, 2435, 2035, 1601, 1010, 489, 34, 5, 1, 1], [1066, 1066, 1066, 1066, 1066, 1066, 2304, 2612, 2973, 3276, 3630, 3743, 3604, 3222, 2761, 2310, 1856, 1386, 831, 338, 8, 1, 0, 0], [1066, 1066, 1066, 1066, 1066, 1066, 2758, 3241, 3637, 4164, 4438, 4419, 4141, 3722, 3263, 2789, 2296, 1803, 1149, 546, 14, 0, 0, 0], [1066, 1066, 1066, 1066, 1066, 1066, 3279, 3784, 4326, 4691, 5038, 5172, 4903, 4451, 3982, 3494, 2839, 2156, 1314, 612, 16, 0, 0, 0], [1066, 1066, 1066, 1066, 1066, 1066, 2089, 2357, 2661, 3016, 3191, 3297, 3291, 3137, 2906, 2588, 2193, 1653, 1015, 413, 49, 25, 9, 9]]
